In [1]:
from custom_dataset.segdataset import InstanceSegmentationDataset
from torch.utils.data import DataLoader
import json

import torch
from torch import nn
from sklearn.metrics import accuracy_score
from tqdm.notebook import tqdm
import os
import evaluate
import logging
from utils import rs_utils
from datetime import datetime
from transformers import SegformerImageProcessor
import numpy as np

In [2]:
#--- root 
root_dir = '/disk3/eric/dataset/Weapon_System/segmentation_pipes'

#--- time
current_time = datetime.now()
formatted_time = current_time.strftime("%Y-%m-%d %H:%M:%S")

In [3]:
#----------
# to test correlation matrix 


#-----------
_VERSION = "206"
_EPOCHS = 50
_N_SHOTS = 5 # 2(==1) or 5 or 10 
_N_INSTANCE = 1
_MODEL_SAVE = True
_MODEL_VERSION = "nvidia/mit-b5"
_MODEL_VERSION_SAVE = _MODEL_VERSION.split("/")[-1]
_BATCH_SIZE = 2
_DEVICE = "cuda:1"
#---------
Config_options = {
    "_VERSION": _VERSION,
    "_EPOCHS": _EPOCHS,
    "_N_SHOTS": _N_SHOTS,
    "_N_INSTANCE": _N_INSTANCE,
    "_MODEL_SAVE": _MODEL_SAVE,
    "_MODEL_VERSION": _MODEL_VERSION,
    "_MODEL_VERSION_SAVE": _MODEL_VERSION_SAVE,
    "_BATCH_SIZE": _BATCH_SIZE,
    "_DEVICE": _DEVICE,
}

In [4]:
# Set up a logger
log_dir = "/home/eric/srcs/FewShotSeg_Lab/FewShotVision_Lab/Segmentation_Pipes/logs"
os.makedirs(log_dir, exist_ok=True)
current_time = datetime.now()
formatted_time = current_time.strftime("%Y-%m-%d %H:%M:%S")
log_file_path = os.path.join(log_dir, f"Version_{_VERSION}_{_MODEL_VERSION_SAVE}_{formatted_time}.log")
logger = rs_utils.setup_logger("FewShotSeg", log_file_path, level=logging.INFO)

#--- 
logger.info("Config Options:\n%s", json.dumps(Config_options, indent=4))

2024-11-28 13:20:03 - FewShotSeg - INFO - Config Options:
{
    "_VERSION": "206",
    "_EPOCHS": 50,
    "_N_SHOTS": 5,
    "_N_INSTANCE": 1,
    "_MODEL_SAVE": true,
    "_MODEL_VERSION": "nvidia/mit-b5",
    "_MODEL_VERSION_SAVE": "mit-b5",
    "_BATCH_SIZE": 2,
    "_DEVICE": "cuda:1"
}


In [5]:
json_file = os.path.join( root_dir, 'train/_annotations.coco.json')
with open(json_file, 'r') as f:
    data = json.load(f)
#--- 
id2label = {
    0:data['categories'][0]['name'],
    1:data['categories'][1]['name'],
    2:data['categories'][2]['name'],
    3:data['categories'][3]['name'],
    4:data['categories'][4]['name']
}
id2label[0] = "background"
label2id = {v: k for k, v in id2label.items()}

In [6]:
label2id

{'background': 0,
 'M2A1Slammer': 1,
 'M5SandstormMLRS': 2,
 'T140Angara': 3,
 'ZamakMRL': 4}

In [7]:
# for fewshot
id2label = {
    0:"background",
    1:"object"
}
label2id = {v: k for k, v in id2label.items()}
label2id

{'background': 0, 'object': 1}

In [8]:
#----------------------
from custom_dataset.segdataset import FewShotSegDataset_v2


image_processor = SegformerImageProcessor(reduce_labels=False,size={"height": 448, "width": 448})

train_dataset = FewShotSegDataset_v2(root_dir=root_dir, image_processor=image_processor,n_shots=_N_SHOTS,n_instance=_N_INSTANCE)
valid_dataset = FewShotSegDataset_v2(root_dir=root_dir, image_processor=image_processor,n_shots=_N_SHOTS,n_instance=_N_INSTANCE, train=False)

#train_dataset = InstanceSegmentationDataset(root_dir=root_dir, image_processor=image_processor)
#valid_dataset = InstanceSegmentationDataset(root_dir=root_dir, image_processor=image_processor, train=False)

train_dataloader = DataLoader(train_dataset, batch_size=_BATCH_SIZE, collate_fn=train_dataset.my_collate_fn, shuffle=True)
valid_dataloader = DataLoader(valid_dataset, batch_size=_BATCH_SIZE, collate_fn=train_dataset.my_collate_fn)

train pairs :  [['Zamak__part_21.png', 'Zamak__part_23.png'], ['Zamak__part_21.png', 'Zamak__part_7.png'], ['Zamak__part_21.png', 'Zamak__part_3.png'], ['Zamak__part_21.png', 'Zamak__part_10.png'], ['M2A1Slammer2__part_24.png', 'M2A1Slammer2__part_23.png'], ['M2A1Slammer2__part_24.png', 'M2A1Slammer2__part_3.png'], ['M2A1Slammer2__part_24.png', 'M2A1Slammer2__part_2.png'], ['M2A1Slammer2__part_24.png', 'M2A1Slammer2__part_14.png'], ['M5Sandstorm__part_26.png', 'M5Sandstorm__part_18.png'], ['M5Sandstorm__part_26.png', 'M5Sandstorm__part_25.png'], ['M5Sandstorm__part_26.png', 'M5Sandstorm__part_24.png'], ['M5Sandstorm__part_26.png', 'M5Sandstorm__part_21.png'], ['M2A1Slammer2__part_23.png', 'M2A1Slammer2__part_24.png'], ['M2A1Slammer2__part_23.png', 'M2A1Slammer2__part_3.png'], ['M2A1Slammer2__part_23.png', 'M2A1Slammer2__part_2.png'], ['M2A1Slammer2__part_23.png', 'M2A1Slammer2__part_14.png'], ['Zamak__part_23.png', 'Zamak__part_21.png'], ['Zamak__part_23.png', 'Zamak__part_7.png'], ['Z

/home/eric/anaconda3/envs/trex/lib/python3.9/site-packages/transformers/models/segformer/image_processing_segformer.py:102: FutureWarning: The `reduce_labels` parameter is deprecated and will be removed in a future version. Please use `do_reduce_labels` instead.
  warnings.warn(


In [9]:
# # 데이터 배치 확인
# for batch in train_dataloader:
#     print(batch["support"]["images"].shape)  # torch.Size([4, 10])
#     print(batch["query"]["labels"].shape)   # torch.Size([4, 15])

In [10]:
# define model
from models.custom_segformer import FewShotFormer

seg_model = FewShotFormer.from_pretrained(_MODEL_VERSION,
                                        num_labels=2,
                                        id2label=id2label,
                                        label2id=label2id,
                                        force_download=False                                       
                                        )

# model freeze

# model freeze 
for param in seg_model.parameters():
    param.requires_grad = False

# decoder unfreeze 
for param in seg_model.decode_head.parameters():
    param.requires_grad = True

/home/eric/anaconda3/envs/trex/lib/python3.9/site-packages/huggingface_hub/file_download.py:797: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
/home/eric/anaconda3/envs/trex/lib/python3.9/site-packages/torch/_utils.py:831: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  return self.fget.__get__(instance, owner)()
Some weights of FewShotFormer were not initialized from the model checkpoint at nvidia/mit-b5 and are newly initialized: ['decode_head.batch_norm.bias', 'decode_head.batch_norm.num_batches_tracked', 'decode_head.batch_norm.running_mean', 'decode_head.batch_norm.running_var', 'decode_hea

In [11]:
BACKBONE_SIZE = "large" # in ("small", "base", "large" or "giant")

backbone_archs = {
    "small": "vits14",
    "base": "vitb14",
    "large": "vitl14",
    "giant": "vitg14",
}
backbone_arch = backbone_archs[BACKBONE_SIZE]
backbone_name = f"dinov2_{backbone_arch}"

dinov2_model = torch.hub.load(repo_or_dir="facebookresearch/dinov2", model=backbone_name)
#backbone_model.to(_DEVICE)

# model freeze 
for param in dinov2_model.parameters():
    param.requires_grad = False

Using cache found in /home/eric/.cache/torch/hub/facebookresearch_dinov2_main
/home/eric/.cache/torch/hub/facebookresearch_dinov2_main/dinov2/layers/swiglu_ffn.py:51: UserWarning: xFormers is not available (SwiGLU)
  warnings.warn("xFormers is not available (SwiGLU)")
/home/eric/.cache/torch/hub/facebookresearch_dinov2_main/dinov2/layers/attention.py:33: UserWarning: xFormers is not available (Attention)
  warnings.warn("xFormers is not available (Attention)")
/home/eric/.cache/torch/hub/facebookresearch_dinov2_main/dinov2/layers/block.py:40: UserWarning: xFormers is not available (Block)
  warnings.warn("xFormers is not available (Block)")


In [12]:
# define metric
metric = evaluate.load("mean_iou")
# define optimizer
optimizer = torch.optim.AdamW(seg_model.parameters(), lr=0.00006)

In [13]:
best_val_iou = 0 


#-- model to device
seg_model = seg_model.to(_DEVICE)
dinov2_model = dinov2_model.to(_DEVICE) 

#---
for epoch in range(_EPOCHS):  # loop over the dataset multiple times
    logger.info(f"Epoch: {epoch}")

    # Training loop
    for idx, batch in enumerate(train_dataloader):
    #   print(batch["support"]["images"].shape)  # torch.Size([4, 10])
    #   print(batch["query"]["labels"].shape)   # torch.Size([4, 15])        
        #--- support & Query
        support_pixel_values, support_labels = batch["support"]['images'].to(_DEVICE), batch["support"]["labels"].to(_DEVICE) 
        query_pixel_values, query_labels = batch["query"]['images'].to(_DEVICE), batch["query"]["labels"].to(_DEVICE) 
        labels = query_labels
        
        #-----
        patch_token = dinov2_model.forward_features(query_pixel_values)
        patch_token = patch_token["x_norm_patchtokens"]
        patch_token = patch_token.reshape([query_pixel_values.shape[0],-1,32,32])

        # zero the parameter gradients
        optimizer.zero_grad()
        # forward + backward + optimize
        outputs = seg_model(pixel_values=support_pixel_values, labels=labels,dino_features = patch_token)
        loss, logits = outputs.loss, outputs.logits

        loss.backward()
        optimizer.step()

        # Evaluate periodically
        #if idx % 10 == 0:
        with torch.no_grad():
            upsampled_logits = nn.functional.interpolate(
                logits, size=labels.shape[-2:], mode="bilinear", align_corners=False
            )
            predicted = upsampled_logits.argmax(dim=1)

            metrics = metric._compute(
                predictions=predicted.cpu(),
                references=labels.cpu(),
                num_labels=len(id2label),
                ignore_index=255,
                reduce_labels=False,  # we've already reduced the labels ourselves
                nan_to_num =0.000001
            )
            logger.info(
                f"Epoch: {epoch}, "
                f"Iteration: {idx}, "
                f"Training Loss: {loss.item():.4f}, "
                f"Mean IoU: {metrics['mean_iou']:.4f}, "
                f"Mean Accuracy: {metrics['mean_accuracy']:.4f}, "
                f"per Category IOU: {metrics['per_category_iou']}"
            )
    #--
    # Validation loop
    val_loss = 0
    val_metrics = {"mean_iou": 0, "mean_accuracy": 0, "per_category_iou":[]}
    for batch in valid_dataloader:
        #--- support & Query
        support_pixel_values, support_labels = batch["support"]['images'].to(_DEVICE), batch["support"]["labels"].to(_DEVICE) 
        query_pixel_values, query_labels = batch["query"]['images'].to(_DEVICE), batch["query"]["labels"].to(_DEVICE) 
        labels = query_labels

        with torch.no_grad():
            #-----
            patch_token = dinov2_model.forward_features(query_pixel_values)
            patch_token = patch_token["x_norm_patchtokens"]
            patch_token = patch_token.reshape([query_pixel_values.shape[0],-1,32,32])

            # zero the parameter gradients
            optimizer.zero_grad()
            # forward + backward + optimize
            outputs = seg_model(pixel_values=support_pixel_values, labels=labels,dino_features = patch_token)
            loss, logits = outputs.loss, outputs.logits
                
            #--------------            
            val_loss += outputs.loss.item()

            upsampled_logits = nn.functional.interpolate(
                logits, size=labels.shape[-2:], mode="bilinear", align_corners=False
            )
            predicted = upsampled_logits.argmax(dim=1)

            batch_metrics = metric._compute(
                predictions=predicted.cpu(),
                references=labels.cpu(),
                num_labels=len(id2label),
                ignore_index=255,
                reduce_labels=False,
                nan_to_num =0.000001
            )
            
            val_metrics["mean_iou"] += batch_metrics["mean_iou"]
            val_metrics["mean_accuracy"] += batch_metrics["mean_accuracy"]
            val_metrics["per_category_iou"].append(batch_metrics["per_category_iou"])
            

    # Average validation loss and metrics
    val_loss /= len(valid_dataloader)
    val_metrics["mean_iou"] /= len(valid_dataloader)
    val_metrics["mean_accuracy"] /= len(valid_dataloader)
    #val_metrics["per_category_iou"] /= len(valid_dataloader)
    val_per_iou = np.asarray(val_metrics["per_category_iou"])
    val_per_iou = np.sum(val_per_iou, axis=0) / val_per_iou.shape[0]

    logger.info(
        f"Epoch : {epoch}, "
        f"Validation Results - Loss: {val_loss:.4f}, "
        f"Mean IoU: {val_metrics['mean_iou']:.4f}, "
        f"Mean Accuracy: {val_metrics['mean_accuracy']:.4f}, "
        f"per Category IOU: {val_per_iou}"
    )

    # Save the model if the validation IoU improves
    if val_metrics["mean_iou"] > best_val_iou:
        best_val_iou = val_metrics["mean_iou"]
        
        if _MODEL_SAVE:
            torch.save(
                seg_model.state_dict(),
                os.path.join(
                    "/disk3/eric/checkpoints/military_fewshot_seg",
                    f"{_VERSION}_{_MODEL_VERSION_SAVE}_fewshotformer_best_epoch_{epoch}_miou_{best_val_iou:.4f}.pt",
                ),
            )
            logger.info("Model saved!")


2024-11-28 13:20:09 - FewShotSeg - INFO - Epoch: 0


filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/images/M5Sandstorm__part_18.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/labels/M5Sandstorm__part_18.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/images/M5Sandstorm__part_25.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/labels/M5Sandstorm__part_25.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/images/T140Angara__part_4.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/labels/T140Angara__part_4.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/images/T140Angara__part_23.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/labels/T140Angara__part_23.png
support_states  torch.Size([2, 768, 112, 112])
query_states  torch.Size([2, 1024, 32, 32])
query_states  torch.Size([2, 768, 112, 112])
torch.Size([2, 64, 112, 112])
mask type :  <class 'torch.Tensor'>
mask

2024-11-28 13:20:10 - FewShotSeg - INFO - Epoch: 0, Iteration: 0, Training Loss: 0.3499, Mean IoU: 0.4832, Mean Accuracy: 0.4986, per Category IOU: [0.96281845 0.003539  ]


filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/images/M2A1Slammer2__part_3.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/labels/M2A1Slammer2__part_3.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/images/M2A1Slammer2__part_14.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/labels/M2A1Slammer2__part_14.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/images/Zamak__part_10.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/labels/Zamak__part_10.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/images/Zamak__part_23.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/labels/Zamak__part_23.png


2024-11-28 13:20:10 - FewShotSeg - INFO - Epoch: 0, Iteration: 1, Training Loss: 0.2217, Mean IoU: 0.4960, Mean Accuracy: 0.4974, per Category IOU: [0.99201561 0.        ]


...

2024-11-28 13:36:12 - FewShotSeg - INFO - Epoch: 6, Iteration: 38, Training Loss: 0.0026, Mean IoU: 0.9502, Mean Accuracy: 0.9934, per Category IOU: [0.99962253 0.90085358]


support_states  torch.Size([2, 768, 112, 112])
query_states  torch.Size([2, 1024, 32, 32])
query_states  torch.Size([2, 768, 112, 112])
torch.Size([2, 64, 112, 112])
mask type :  <class 'torch.Tensor'>
mask shape :  torch.Size([2, 448, 448])
weighted_support_states torch.Size([2, 768, 112, 112])
all_factors :  torch.Size([2, 2368, 112, 112])
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/images/M5Sandstorm__part_25.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/labels/M5Sandstorm__part_25.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/images/M5Sandstorm__part_24.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/labels/M5Sandstorm__part_24.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/images/Zamak__part_10.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/labels/Zamak__part_10.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/

2024-11-28 13:36:13 - FewShotSeg - INFO - Epoch: 6, Iteration: 39, Training Loss: 0.0049, Mean IoU: 0.9534, Mean Accuracy: 0.9857, per Category IOU: [0.99967511 0.90707648]


filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/images/M2A1Slammer2__part_14.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/labels/M2A1Slammer2__part_14.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/images/Zamak__part_18.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/labels/Zamak__part_18.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/images/M2A1Slammer2__part_14.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/labels/M2A1Slammer2__part_14.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/images/M5Sandstorm__part_17.png
filename /disk3/eric/dataset/Weapon_System/segmentation_pipes/train/labels/M5Sandstorm__part_17.png
support_states  torch.Size([2, 768, 112, 112])
query_states  torch.Size([2, 1024, 32, 32])
query_states  torch.Size([2, 768, 112, 112])
torch.Size([2, 64, 112, 112])
mask type :  <class 'torch.Tensor'>
mask s

KeyboardInterrupt: 

In [ ]:
import torch.nn.functional as F
supp_feat = torch.rand([2, 768, 112, 112])
mask = torch.rand([2, 768, 112, 112])


avg_pool2d = F.avg_pool2d(mask, (supp_feat.size()[2], supp_feat.size()[3])) 

In [ ]:
feat_h, feat_w = supp_feat.shape[-2:][0], supp_feat.shape[-2:][1]

In [ ]:
feat_h

112

In [ ]:
area = avg_pool2d * feat_h * feat_w

In [ ]:
area.shape

torch.Size([2, 768, 1, 1])

In [ ]:
area.shape

torch.Size([2, 768, 1, 1])

In [ ]:
supp_feat.shape[-2:]

torch.Size([112, 112])